In [38]:
import pandas as pd
import pandas as pd
import numpy as np
from keras.utils import np_utils
from sklearn.metrics import roc_auc_score, confusion_matrix, accuracy_score, make_scorer, f1_score,precision_score,recall_score
from sklearn.preprocessing import MinMaxScaler
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import GridSearchCV
import matplotlib.pyplot as plt
import itertools
from sklearn.metrics import classification_report, plot_confusion_matrix,fbeta_score, make_scorer
import seaborn as sns
from sklearn.model_selection import KFold
from sklearn.model_selection import StratifiedKFold
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.utils import np_utils
import time

In [39]:
def print_distribution(arr, print_nl=True):
    arr = np.unique(arr, return_counts=True)[1] / len(arr)
    for i in range(arr.shape[0]):
        print("Classe %d: %.2f%%" %(i, arr[i]*100))

    if print_nl:
        print("\n")

In [40]:
def taste(quality):
  if quality <= 5:
    return 0
  elif quality > 5 and quality <= 7:
    return 1
  else:
    return 2

In [41]:
time_begin = time.time()
data = pd.read_csv("wine_quality.csv")
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6497 entries, 0 to 6496
Data columns (total 12 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   fixed.acidity         6497 non-null   float64
 1   volatile.acidity      6497 non-null   float64
 2   citric.acid           6497 non-null   float64
 3   residual.sugar        6497 non-null   float64
 4   chlorides             6497 non-null   float64
 5   free.sulfur.dioxide   6497 non-null   float64
 6   total.sulfur.dioxide  6497 non-null   float64
 7   density               6497 non-null   float64
 8   pH                    6497 non-null   float64
 9   sulphates             6497 non-null   float64
 10  alcohol               6497 non-null   float64
 11  quality               6497 non-null   int64  
dtypes: float64(11), int64(1)
memory usage: 609.2 KB


In [42]:
new_data = data
new_data["taste"] = data["quality"].apply(taste)

In [43]:
new_data

fixed.acidity  volatile.acidity  citric.acid  residual.sugar  chlorides  \
0               7.4              0.70         0.00             1.9      0.076   
1               7.8              0.88         0.00             2.6      0.098   
2               7.8              0.76         0.04             2.3      0.092   
3              11.2              0.28         0.56             1.9      0.075   
4               7.4              0.70         0.00             1.9      0.076   
...             ...               ...          ...             ...        ...   
6492            6.2              0.21         0.29             1.6      0.039   
6493            6.6              0.32         0.36             8.0      0.047   
6494            6.5              0.24         0.19             1.2      0.041   
6495            5.5              0.29         0.30             1.1      0.022   
6496            6.0              0.21         0.38             0.8      0.020   

      free.sulfur.dioxide  total.sulfur.dioxide  density    pH  sulphates  \
0                    11.0                  34.0  0.99780  3.51       0.56   
1                    25.0                  67.0  0.99680  3.20       0.68   
2                    15.0                  54.0  0.99700  3.26       0.65   
3                    17.0                  60.0  0.99800  3.16       0.58   
4                    11.0                  34.0  0.99780  3.51       0.56   
...                   ...                   ...      ...   ...        ...   
6492                 24.0                  92.0  0.99114  3.27       0.50   
6493                 57.0                 168.0  0.99490  3.15       0.46   
6494                 30.0                 111.0  0.99254  2.99       0.46   
6495                 20.0                 110.0  0.98869  3.34       0.38   
6496                 22.0                  98.0  0.98941  3.26       0.32   

      alcohol  quality  taste  
0         9.4        5      0  
1         9.8        5      0  
2         9.8        5      0  
3         9.8        6      1  
4         9.4        5      0  
...       ...      ...    ...  
6492     11.2        6      1  
6493      9.6        5      0  
6494      9.4        6      1  
6495     12.8        7      1  
6496     11.8        6      1  

[6497 rows x 13 columns]

## Divisão de base de dados e separação de base

In [44]:
X = new_data.iloc[:, 0:11].values
y = new_data.iloc[:, 12].values

In [45]:
print("Proporções por classe no dataset em geral:")
print_distribution(y)

kf = StratifiedKFold(n_splits=10, shuffle=True, random_state=199)
fold = 0
for train, test in kf.split(X, y):
    print("Fold %d" %(fold))
    print_distribution(y[train], print_nl=(fold != 2))
    fold += 1

Proporções por classe no dataset em geral:
Classe 0: 36.69%
Classe 1: 60.26%
Classe 2: 3.05%


Fold 0
Classe 0: 36.69%
Classe 1: 60.27%
Classe 2: 3.04%


Fold 1
Classe 0: 36.69%
Classe 1: 60.27%
Classe 2: 3.04%


Fold 2
Classe 0: 36.69%
Classe 1: 60.27%
Classe 2: 3.04%
Fold 3
Classe 0: 36.69%
Classe 1: 60.27%
Classe 2: 3.04%


Fold 4
Classe 0: 36.70%
Classe 1: 60.25%
Classe 2: 3.04%


Fold 5
Classe 0: 36.70%
Classe 1: 60.25%
Classe 2: 3.04%


Fold 6
Classe 0: 36.70%
Classe 1: 60.25%
Classe 2: 3.04%


Fold 7
Classe 0: 36.70%
Classe 1: 60.24%
Classe 2: 3.06%


Fold 8
Classe 0: 36.70%
Classe 1: 60.24%
Classe 2: 3.06%


Fold 9
Classe 0: 36.70%
Classe 1: 60.26%
Classe 2: 3.04%




In [46]:
kf_accuracy = list()
kf_conf_mat = list()
kf_precision = list()
kf_f1 = list()
kf_recall = list()
kf_roc = list()

In [47]:
def createANN(epochs,activation, neurons):
    classifier = Sequential()
    classifier.add(Dense(units=neurons, activation=activation,input_dim=11))
    classifier.add(Dropout(0.1))
    classifier.add(Dense(units=neurons, activation=activation))
    classifier.add(Dropout(0.1))
    classifier.add(Dense(units=3, activation="softmax"))
    classifier.compile(optimizer="adam", loss="sparse_categorical_crossentropy",
                       metrics=["accuracy"])
    classifier.fit(X_train, y_train, batch_size=32, epochs=epochs)
    return classifier

In [48]:
for train_ix, test_ix in kf.split(X,y):
    X_train, X_test = X[train_ix, :], X[test_ix, :]
    y_train, y_test = y[train_ix], y[test_ix]
    classifier = KerasClassifier(build_fn=createANN)
    parameters={"epochs": [10,20],
                "activation":["linear","relu"],
                "neurons": [4,8]}
    # parâmetros para teste do gridsearch
    search = GridSearchCV(estimator=classifier, param_grid=parameters, scoring="accuracy", cv=10, refit=True)
    # executar e salvar melhores parâmetros do grisearch
    result = search.fit(X_train, y_train)
    # teste dos melhores parâmetros
    best_model = result.best_estimator_
    # evaluate model on the hold out dataset
    predicted_y = best_model.predict(X_test)
    #transformação de itens para cálculo do ROC
    y_test_dummy = np_utils.to_categorical(y_test)
    y_test_dummy
    predicted_y_dummy = np_utils.to_categorical(predicted_y)
    predicted_y_dummy
    # métricas do modelo
    acc = accuracy_score(y_test, predicted_y)
    conf_mat = confusion_matrix(y_test, predicted_y)
    precision = precision_score(y_test, predicted_y, average = "macro")
    f1 = f1_score(y_test, predicted_y, average = "macro")
    recall = recall_score(y_test, predicted_y, average = "macro")
    roc = roc_auc_score(y_test_dummy,predicted_y_dummy,multi_class="ovo",average = "macro")
    # armazenamento de métricas
    kf_accuracy.append(acc)
    kf_conf_mat.append(conf_mat)
    kf_precision.append(precision)
    kf_f1.append(f1)
    kf_recall.append(recall)
    kf_roc.append(roc)
    #métricas
    print(">acc=%.3f,>prec=%.3f,>f1=%.3f,>rec=%.3f,>roc=%.3f, est=%.3f, cfg=%s" % (acc,precision,f1,recall,roc, result.best_score_, result.best_params_))
    print(conf_mat)

C:\Users\cfpc2\AppData\Local\Temp/ipykernel_2256/1221881577.py:4: DeprecationWarning: KerasClassifier is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead.
  classifier = KerasClassifier(build_fn=createANN)


Epoch 1/10
183/183 [==============================] - 1s 2ms/step - loss: 60.5705 - accuracy: 0.2642
Epoch 2/10
183/183 [==============================] - 0s 1ms/step - loss: 11.1413 - accuracy: 0.4127
Epoch 3/10
183/183 [==============================] - 0s 2ms/step - loss: 6.2644 - accuracy: 0.4315
Epoch 4/10
183/183 [==============================] - 0s 1ms/step - loss: 3.6468 - accuracy: 0.4339
Epoch 5/10
183/183 [==============================] - 0s 1ms/step - loss: 2.1288 - accuracy: 0.4761
Epoch 6/10
183/183 [==============================] - 0s 1ms/step - loss: 1.7147 - accuracy: 0.5081
Epoch 7/10
183/183 [==============================] - 0s 1ms/step - loss: 1.4575 - accuracy: 0.5442
Epoch 8/10
183/183 [==============================] - 0s 1ms/step - loss: 1.3938 - accuracy: 0.5362
Epoch 9/10
183/183 [==============================] - 0s 1ms/step - loss: 1.3074 - accuracy: 0.5447
Epoch 10/10
183/183 [==============================] - 0s 1ms/step - loss: 1.2330 - accuracy: 0.54

183/183 [==============================] - 0s 673us/step - loss: 2.2774 - accuracy: 0.5088
Epoch 3/10
183/183 [==============================] - 0s 915us/step - loss: 1.3563 - accuracy: 0.5273
Epoch 4/10
183/183 [==============================] - 0s 1ms/step - loss: 1.1032 - accuracy: 0.5589
Epoch 5/10
183/183 [==============================] - 0s 1ms/step - loss: 0.9515 - accuracy: 0.5765
Epoch 6/10
183/183 [==============================] - 0s 1ms/step - loss: 0.8914 - accuracy: 0.5752
Epoch 7/10
183/183 [==============================] - 0s 1ms/step - loss: 0.8615 - accuracy: 0.5801
Epoch 8/10
183/183 [==============================] - 0s 857us/step - loss: 0.8178 - accuracy: 0.5888
Epoch 9/10
183/183 [==============================] - 0s 1ms/step - loss: 0.8182 - accuracy: 0.5870
Epoch 10/10
183/183 [==============================] - 0s 656us/step - loss: 0.7974 - accuracy: 0.6015
Epoch 1/10
165/165 [==============================] - 0s 839us/step - loss: 0.7943 - accuracy: 0.5950


183/183 [==============================] - 0s 1ms/step - loss: 1.7094 - accuracy: 0.5444
Epoch 4/10
183/183 [==============================] - 0s 1ms/step - loss: 1.2605 - accuracy: 0.5646
Epoch 5/10
183/183 [==============================] - 0s 1ms/step - loss: 1.0835 - accuracy: 0.5726
Epoch 6/10
183/183 [==============================] - 0s 1ms/step - loss: 0.9353 - accuracy: 0.5853
Epoch 7/10
183/183 [==============================] - 0s 1ms/step - loss: 0.8670 - accuracy: 0.5861
Epoch 8/10
183/183 [==============================] - 0s 1ms/step - loss: 0.8277 - accuracy: 0.5943
Epoch 9/10
183/183 [==============================] - 0s 1ms/step - loss: 0.8025 - accuracy: 0.5950
Epoch 10/10
183/183 [==============================] - 0s 1ms/step - loss: 0.7927 - accuracy: 0.5996
Epoch 1/10
165/165 [==============================] - 0s 1ms/step - loss: 0.7951 - accuracy: 0.5974
Epoch 2/10
165/165 [==============================] - 0s 1ms/step - loss: 0.7874 - accuracy: 0.5981
Epoch 3/10

183/183 [==============================] - 0s 1ms/step - loss: 2.3920 - accuracy: 0.5146
Epoch 5/10
183/183 [==============================] - 0s 1ms/step - loss: 1.6971 - accuracy: 0.5098
Epoch 6/10
183/183 [==============================] - 0s 1ms/step - loss: 1.3309 - accuracy: 0.5290
Epoch 7/10
183/183 [==============================] - 0s 1ms/step - loss: 1.1587 - accuracy: 0.5454
Epoch 8/10
183/183 [==============================] - 0s 1ms/step - loss: 1.0175 - accuracy: 0.5603
Epoch 9/10
183/183 [==============================] - 0s 1ms/step - loss: 0.9577 - accuracy: 0.5647
Epoch 10/10
183/183 [==============================] - 0s 1ms/step - loss: 0.9110 - accuracy: 0.5762
Epoch 1/10
165/165 [==============================] - 0s 1ms/step - loss: 0.8528 - accuracy: 0.5943
Epoch 2/10
165/165 [==============================] - 0s 1ms/step - loss: 0.8446 - accuracy: 0.5960
Epoch 3/10
165/165 [==============================] - 0s 1ms/step - loss: 0.8291 - accuracy: 0.5945
Epoch 4/10

...

183/183 [==============================] - 2s 3ms/step - loss: 2.5079 - accuracy: 0.5154
Epoch 2/10
183/183 [==============================] - 0s 3ms/step - loss: 1.1900 - accuracy: 0.5508
Epoch 3/10
183/183 [==============================] - 1s 3ms/step - loss: 0.9624 - accuracy: 0.5658
Epoch 4/10
183/183 [==============================] - 0s 3ms/step - loss: 0.8771 - accuracy: 0.5821
Epoch 5/10
183/183 [==============================] - 0s 3ms/step - loss: 0.8202 - accuracy: 0.6017
Epoch 6/10
183/183 [==============================] - 0s 3ms/step - loss: 0.8011 - accuracy: 0.6017
Epoch 7/10
183/183 [==============================] - 1s 3ms/step - loss: 0.7786 - accuracy: 0.6156
Epoch 8/10
183/183 [==============================] - 1s 3ms/step - loss: 0.7751 - accuracy: 0.6134
Epoch 9/10
183/183 [==============================] - 1s 3ms/step - loss: 0.7667 - accuracy: 0.6214
Epoch 10/10
183/183 [==============================] - 1s 3ms/step - loss: 0.7616 - accuracy: 0.6170
Epoch 1/10

165/165 [==============================] - 0s 3ms/step - loss: 0.7579 - accuracy: 0.6145
Epoch 3/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7559 - accuracy: 0.6145
Epoch 4/20
165/165 [==============================] - 1s 3ms/step - loss: 0.7504 - accuracy: 0.6145
Epoch 5/20
165/165 [==============================] - 1s 3ms/step - loss: 0.7513 - accuracy: 0.6145
Epoch 6/20
165/165 [==============================] - 1s 3ms/step - loss: 0.7410 - accuracy: 0.6145
Epoch 7/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7382 - accuracy: 0.6103
Epoch 8/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7308 - accuracy: 0.6038
Epoch 9/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7281 - accuracy: 0.6019
Epoch 10/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7234 - accuracy: 0.6118
Epoch 11/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7184 - accuracy: 0.6282
Epoch 12/

165/165 [==============================] - 0s 2ms/step - loss: 0.7775 - accuracy: 0.6099
Epoch 4/20
165/165 [==============================] - 0s 2ms/step - loss: 0.7773 - accuracy: 0.6099
Epoch 5/20
165/165 [==============================] - 0s 2ms/step - loss: 0.7774 - accuracy: 0.6099
Epoch 6/20
165/165 [==============================] - 0s 2ms/step - loss: 0.7772 - accuracy: 0.6099
Epoch 7/20
165/165 [==============================] - 0s 2ms/step - loss: 0.7771 - accuracy: 0.6099
Epoch 8/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7771 - accuracy: 0.6099
Epoch 9/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7771 - accuracy: 0.6099
Epoch 10/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7771 - accuracy: 0.6099
Epoch 11/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7770 - accuracy: 0.6099
Epoch 12/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7770 - accuracy: 0.6099
Epoch 13

165/165 [==============================] - 0s 3ms/step - loss: 0.7799 - accuracy: 0.6065
Epoch 5/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7805 - accuracy: 0.6010
Epoch 6/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7736 - accuracy: 0.6061
Epoch 7/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7753 - accuracy: 0.6076
Epoch 8/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7726 - accuracy: 0.6038
Epoch 9/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7748 - accuracy: 0.6059
Epoch 10/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7752 - accuracy: 0.6048
Epoch 11/20
165/165 [==============================] - 0s 2ms/step - loss: 0.7703 - accuracy: 0.6111
Epoch 12/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7712 - accuracy: 0.6031
Epoch 13/20
165/165 [==============================] - 0s 3ms/step - loss: 0.7711 - accuracy: 0.6080
Epoch 1

KeyboardInterrupt: 

In [22]:
print("Accuracy: %.3f (%.3f)" % (np.mean(kf_accuracy), np.std(kf_accuracy)))
print("Precision: %.3f (%.3f)" % (np.mean(kf_precision), np.std(kf_precision)))
print("F1-score: %.3f (%.3f)" % (np.mean(kf_f1), np.std(kf_f1)))
print("Recall: %.3f (%.3f)" % (np.mean(kf_recall), np.std(kf_recall)))
print("ROC: %.3f (%.3f)" % (np.mean(kf_roc), np.std(kf_roc)))

Accuracy: 0.600 (0.051)
Precision: 0.362 (0.080)
F1-score: 0.314 (0.046)
Recall: 0.351 (0.030)
ROC: 0.522 (0.029)


In [23]:
kf_conf_mat

[array([[ 45, 190,   4],
        [ 37, 353,   1],
        [  0,  20,   0]], dtype=int64),
 array([[ 44, 191,   4],
        [ 48, 340,   3],
        [  0,  20,   0]], dtype=int64),
 array([[  0, 238,   1],
        [  0, 388,   3],
        [  0,  20,   0]], dtype=int64),
 array([[  3, 236,   0],
        [ 13, 378,   0],
        [  0,  20,   0]], dtype=int64),
 array([[ 36, 202,   0],
        [ 34, 358,   0],
        [  0,  20,   0]], dtype=int64),
 array([[ 12, 226,   0],
        [  5, 387,   0],
        [  0,  20,   0]], dtype=int64),
 array([[ 30, 208,   0],
        [ 17, 375,   0],
        [  0,  20,   0]], dtype=int64),
 array([[ 77, 148,  13],
        [156, 228,   8],
        [  7,  12,   0]], dtype=int64),
 array([[ 31, 207,   0],
        [ 26, 366,   0],
        [  0,  19,   0]], dtype=int64),
 array([[ 82, 154,   2],
        [ 28, 363,   0],
        [  0,  20,   0]], dtype=int64)]

In [24]:
np.mean(kf_conf_mat,axis=0)

array([[ 36. , 200. ,   2.4],
       [ 36.4, 353.6,   1.5],
       [  0.7,  19.1,   0. ]])

In [25]:
time_end = time.time()
print((time_end - time_begin)/60)

27.32143104871114
